In [1]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import tifffile as tf
from scipy.ndimage.filters import gaussian_filter1d as gaussian
from glob import glob
from scipy.signal import savgol_filter, medfilt
import matplotlib.ticker as ticker
from scipy.optimize import curve_fit

In [2]:
# 1. load data into pandas data frame

# 2. convert data from I(t) to c_i(t) via equation for G quadruplex binding
    # - find t0
    # - 
# 3. calculate dc_i/dt for each GUV

# 4. calculate background intensity and convert this to c_0(t) via g quadruplex binding model

# 5. plot dc_/dt/A_GUV vs c_0-c_i (expect to see a positive linear relationship)


# as data includes actual G4 background for GUV permeability and later Gramicidin A experiments, start with these experiments


In [3]:
App = 3.16 #um^2
Amin= 75*App*1e-12 #m^2


# G quadruplex model binding



def exp_I(t,k,c):
    
    k_b = 8.8
    A = 1
#     c = 0.98
#     c = 0.46
    return c+(1-c)/(A*k_b*(1-np.exp(-k*t))**2+1)


def inv(I, k = 8.8,A = 0.5):
    
    if I > 1:
        return 0
    
    elif I < A:
        return 1
        
    else:
        return np.sqrt((1/k)*((1-A)/(I-A)-1))

#smoothing configs

sigma = 30




# Calibration model fit


## **If you have already fitted a calibration function and saved the parameters skip this section**

## Discussion of binding model deficiencies

1. **Binding model**

By considering the binding reaction G4 + nK <=> complex we can develop a model to fit the calibration experiment for the g quadruplex sensor.

It was found that in an excess of potassium the 'completely folded' g quadruplex goes to 0.5 of its free intensity. I assume then that in the intermediate concentrations of potassium, there is a mixture of unfolded and folded g quadruplex. 

Therefore $I = I_0[G4]_{free} + 0.5I_0[G4]_{folded}$,

by assuming on the addition of potassium the system reaches equilibrium much faster than the timescales of the transport, then we gain  $\frac{I}{I_0} = 0.5(\frac{1}{1+K_b[K]^2} +1)$

$K_b$ is found by fitting this function to the calibration.

2. **Problems**

As this function plateaus at 0.5, defining a sensible inverse that can practicably applied to a noisy intensity measurement (to measure [K]  is difficult. As noisy variations near $\frac{I}{I_0}$ cause wild swings in the concentration.

3. **Solution**

Therefore we surpress these swings by defining an approximate inverse that does not diverge at the edges.

We do this by creating an effective intensity of the folded g quadruplex that is artificially lower than the believe value. Therefore our calibration model becomes:

$I = I_0[G4]_{free} + c_{eff}I_0[G4]_{folded}$, where $c_{eff} < 0.5$.
    
$\frac{I}{I_0} = c_{eff} + \frac{1-c_{eff}}{K_b[K]^2 +1}$

**This doesn't really work as we still have a blowing up value, need to define a nicer function**

Define a polynomial approximation that is similar

In [4]:
# finding a suitable calibration

calib_data = pd.read_csv('../20210323_KCLFAMG4Q0to20mMCalib/RelIntensG41Concentration.csv')

In [9]:
%matplotlib qt
I= np.linspace(1,0.2,100)

fig, ax = plt.subplots(1,1)

ax.scatter(calib_data['Rel. Intes'],calib_data['K conc [mM]'],marker = '+',s = 5)

legend = []

# fit a polynomial


fit = np.polyfit(-np.log(calib_data['Rel. Intes'].iloc[:-1]),calib_data['K conc [mM]'].iloc[:-1],3)

def fit_func(I,fit):
    
    c = np.zeros_like(I)
    
    for i in range(1,len(fit)+1):

        c += fit[i-1]*(-np.log(I))**(len(fit)-i)
        print(len(fit)-i)
    return c



ax.plot(I,fit_func(I,fit))

legend.append('Calibration')

def model_fit(cK,kb,c):
    return c + (1-c)/(kb*cK**2+1)

params = curve_fit(model_fit,calib_data['K conc [mM]'],calib_data['Rel. Intes'], p0 = [8.8,0.45])

cK_bar = np.linspace(0,2)
I_bar = model_fit(cK_bar,params[0][0],params[0][1])

ax.set_xlim([0.35,1.05])
ax.plot(I_bar,cK_bar,label = 'Model')
legend.append('Model')

l  = plt.errorbar(calib_data['Rel. Intes'],calib_data['K conc [mM]'],rel_errorK*calib_data['K conc [mM]'],drelI,c = 'k')

ax.set_xticks([0.4,0.6,0.8,1])
ax.set_xticklabels([0.4,0.6,0.8,1],fontsize  = 15)

ax.set_yticks([0,1,2])
ax.set_yticklabels([0,1,2],fontsize = 15)
ax.set_ylim([-0.1,2.1])
plt.tick_params(direction = 'in',top = True,bottom = True,right = True, left = True,length = 5)
ax.set_xlabel('Rel Intensity [a.u]',fontsize = 18)
ax.set_ylabel('[K]/[mM]',fontsize = 18)
l[0].remove()
plt.legend(legend)



3
2
1
0


In [30]:
help(l.remove)

Help on method remove in module matplotlib.container:

remove() method of matplotlib.container.ErrorbarContainer instance



# Errors in calibration

**Errors are mainly due to the focal plane measured**


In [6]:
raw_data = pd.read_csv('../20210323_KCLFAMG4Q0to20mMCalib/1uM/Intensities0-2mM.csv')

In [7]:
n = 512**2

print(raw_data['StdDev']/np.sqrt(n))

dI = raw_data['StdDev']/np.sqrt(n)
drelI = dI/raw_data['Mean']

drelI = drelI*10

0    2.244234
1    2.140793
2    1.921438
3    1.709535
4    1.638162
5    1.617246
Name: StdDev, dtype: float64


# Potassium concentration errors

In [8]:
rel_errorK = 0.02



# Load calibration function parameters and define function



In [5]:
fitsdf = pd.read_csv('../Calibrations/Calibration_approx_fit_params.csv')

fit = fitsdf['Fitting Params']

def fit_func(I,fit):
    
    c = np.zeros_like(I)
    
    for i in range(1,len(fit)+1):

        c += fit[i-1]*(-np.log(I))**(len(fit)-i)
        print(len(fit)-i)
    return c


# Single GUV modelling

In [6]:
t0 = 65
t1 = -1
dt = 15/60

In [7]:
# load 260pM Gramicidin A experiment

dfI = pd.read_csv('../KineticsofLeakageGramicidin/collatedIabs260pM.csv')
dfA = pd.read_csv('../KineticsofLeakageGramicidin/collatedIabs260pM.csv')

In [8]:
dfI = dfI.iloc[:,1:]
dfA = dfA.iloc[:,1:]

In [9]:
dfA = dfA.fillna(0)
dfI = dfI.fillna(0)

# Remove small detected objects, most likely not GUVs

**check that the size is appropriate for the experiment**

In [10]:
# remove traces for GUVs below a certain area

for col in dfI.columns:
    
    if col in dfA.columns:
        area = 1e-12*App*np.mean(dfA[col].iloc[:30])
        
        if area < Amin:
            dfI.pop(col)
            dfA.pop(col)

# Remove intensity curves with sudden drops
## These are likely from GUVs suddenly escaping the trap

In [11]:

def remove_burst_events(data,threshold = 0.45):
    
    for column in data.columns:
        
        if len(data[column][data[column] < threshold]) >=1:
            data.pop(column)
            

In [12]:
%matplotlib qt
fig, ax = plt.subplots(1,1)

for col in dfI.columns:
    ax.plot(dfI[col])

In [13]:
# normalise intensities

for col in dfI.columns:
    dfI[col] = dfI[col]/np.mean(dfI[col][:30])
remove_burst_events(dfI)

# Smooth data

## Smoothing strategy

1. In experiments where there was relatively fast decay in intensity initially, but slows down (as exponential decays do..), yet there is still a lot of noise, it may be necessary to smooth different regions with different 'cutoff's.
When the intensity has dropped, the signal to noise drops. What's more during the slower period of intensity decay, there is increasing likelihood that some long timescale event will have happened to distort the data. This long timescale noise may be of a similar timescale to the 'signal' in the early period of rapid decay. 

2. The **solution** chosen here, is to have the user select a timepoint to bisect the time traces. The early period up until that timepoint is smoothed with the 1st user input smoothing parameter (usually between 11-21). Then the later period of slow decay is smoother with much larger smoothing settings (50-80). In order to ensure a smooth 'stitching' of these differently smoothed traces, we concatenate and repeat the smoothing with the smallest of the two specified smoothing parameters.

In [14]:
def smooth_decay(I,t0,t1=-1,smoothing_0 = 19,smoothing_1 = 81):
    
    
    if smoothing_0 > t1-t0 and t1 != -1:
        raise ValueError('Smoothing parameter cannot be greater than input data')
    
    smoothed_decay_0 = I.iloc[t0:t1]
    
    smoothed_decay_0 = savgol_filter(smoothed_decay_0,smoothing_0,1)
    
    if t1 != -1:
        
        smoothed_decay_1 = I.iloc[t1:]
        smoothed_decay_1  = savgol_filter(smoothed_decay_1,smoothing_1,1)
        
        smoothed_decay = np.concatenate((smoothed_decay_0,smoothed_decay_1))
    else:
        smoothed_decay = smoothed_decay_0
                               
    final_smoothed_decay = savgol_filter(smoothed_decay,smoothing_0,1)
    return final_smoothed_decay
                                   

In [39]:
#Check smoothing still fits data
#
num = 8
fig,axs = plt.subplots(1,num)

for i,col in enumerate(dfI.columns[np.random.randint(0,len(dfI.columns),num)]):
    #
    axs[i].plot(dfI[col].iloc[t0:].to_numpy())
    
    axs[i].plot(smooth_decay(dfI[col],t0,t1 = 220,smoothing_0=51,smoothing_1=101))
    

# Use calibration inverse to convert I to [K]

In [40]:
dfC_dict = {}

# can't exploit numpy broadcasting

for col in dfI.columns:
    
    smoothed_decay = smooth_decay(dfI[col],t0,t1)
#     print(smoothed_decay)
#     normalised_sd = smoothed_decay/np.mean(smoothed_decay[:30])
    
    cs = []
    for I in smoothed_decay:
#         print(I)
        cs.append(fit_func(I,fit))
    
    
    dfC_dict[col] = cs
    
dfC = pd.DataFrame(dfC_dict)

3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


...

0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1


2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


In [15]:
%matplotlib qt

fig, axs = plt.subplots(1,3)

t = dt*np.arange(0,len(dfC))
for col in dfC.columns:
    
    
    axs[0].plot(t,dfC[col])
#     axs[1].plot(t,medfilt(dfI[col].iloc[t0:t1],31))
    axs[2].plot(t,dfI[col].iloc[t0:t1])

    for ax in axs:
        ax.set_ylim([0,1])



In [13]:
# find representative background concentration variation

# tifs = glob('/media/marcus/9C33-6BBD/20210920_GramA_260pM07_3nM815_1mMKCl_1/260pM/*.tif')

# bgs = []

# fig, ax = plt.subplots(1,1)

# for tif in tifs:
    
#     vid = tf.TiffFile(tif)
    
#     frames = vid.asarray()
    
#     bg = np.median(frames,axis  =(1,2))
#     bg = np.array(bg)/np.max(bg)
#     bgs.append(bg)
    
    
#     ax.plot(bg)

# This confirms that the normalised background is the same for each chamber. Suggesting potassium concs are identical between chambers



In [41]:
# filter concentration data by gradient
# if 

fig, axs = plt.subplots(1,2)

for col in dfC.columns:
    
    grad = np.gradient(dfC[col])
    
    if len(grad[grad <= -0.0009])/len(grad) > 0.05:
        dfC.pop(col)
        continue
    axs[0].hist(grad,15)
    axs[1].plot(dfC[col])

In [58]:
tifs = glob('/media/marcus/9C33-6BBD/20210427_OmpF_PCPG_KCL_Flush_2-20210427T184510Z-002/20210427_OmpF_PCPG_KCL_Flush_2/*.tif')
tif = tifs[-1]

vid = tf.TiffFile(tif)

frames = vid.asarray()
bg = np.median(frames,axis = (1,2))

bg = np.array(bg)-np.mean(bg[:30])
bg = bg/np.max(bg)

smoothed_bg = medfilt(bg,11)

OME series: not an ome-tiff master file


In [131]:
# c_bg = []
# for x in bg[360+t0:]:
#     c_bg.append(inv(x))

In [132]:
# fig, axs = plt.subplots(1,2)


# smoothed_background = gaussian(c_bg,sigma)
# axs[0].plot(smoothed_background)
# axs[1].plot(bg[360+t0:])

In [80]:
# drift in the background intensity over time, once the potassium has arrived, is causing a drifting predicted potassium concentration
# this is unlikely to be the case in reality.
# Therefore the best thing may be to just assume that after an initial 80 frame boundary region (20 mins) for this exp
# the potassium concentration externally reaches 1mM.


In [42]:
# calculating c_ext - c_i

dfdeltaC_dict = {}

for col in dfC:
    
    dfdeltaC_dict[col] = 1-dfC[col]
    
dfdeltaC = pd.DataFrame(dfdeltaC_dict)

In [43]:
fig, axC = plt.subplots(1,1)

delete_cols = []

for col in dfdeltaC.columns:
    graddeltaC = np.gradient(dfdeltaC[col])
    
    
#     if len(graddeltaC[graddeltaC > 0]) > 1:
#         delete_cols.append(col)
#         continue
        
    axC.plot(dfdeltaC[col])

In [19]:
for col in delete_cols:
    dfdeltaC.pop(col)

In [44]:
# now calculate J

# J = (1/A)*dN/dt = R/3* dc_i/dt

dfJ_dict = {}


for col in dfdeltaC:
    
    if col in dfA:
        print(col)
        delta_c = np.gradient(dfC[col],dt)/60 #molm^-3s^-1
        print(dfC[col])
        A = np.mean(dfA[col].iloc[:30])*App*1e-12 #m^2
#         if A < Amin:
#             continue
        R = np.sqrt(A/np.pi) #m
        
        dfJ_dict[col] = R/3*delta_c #molm^-2s^-1
        

dfJ = pd.DataFrame(dfJ_dict)




11003
0      0.016224921574595073
1      0.015546861088376902
2      0.014868101003294894
3      0.014188641047094053
4      0.013508480949223984
5      0.012827620440834707
6      0.012146059254770716
7      0.011463797125565944
8       0.01078083378943874
9      0.010097168984285271
10     0.009326484581349166
11     0.008467251963586494
12     0.007797768387778779
13     0.007346970434768451
14     0.006810359980343384
15     0.006319856800695945
16     0.006111492648614992
17     0.006160552868416199
18     0.006430714666829154
19     0.007149419400479668
20     0.007686305226570906
21        0.007982849117694
22     0.008101673672212747
23     0.008583991512401943
24     0.009421720064202839
25     0.010189918093448436
26     0.010866523674875863
27     0.011523423236112027
28     0.012078457523795362
29     0.012855618525659456
               ...         
504     0.05951394230087095
505     0.05987322372342764
506    0.060111781820340895
507    0.060241468659829586
508     0.0602

Name: 15014, Length: 534, dtype: object
15016
0      -0.00010732584448254218
1      -0.00040660629972638033
2       -0.0007060177333223223
3       -0.0010055601640223816
4       -0.0013052336105230538
5       -0.0016050380914668172
6       -0.0019049736254407737
7       -0.0022050402309781573
8        -0.002505237926556968
9        -0.002805566730601841
10       -0.003143714566073123
11      -0.0034955606608169446
12      -0.0038389421408584704
13       -0.004151411210052332
14       -0.004408209902881054
15       -0.004548749682476448
16       -0.004510083208153165
17       -0.004263066293734735
18       -0.003924369100523123
19      -0.0033699013696379286
20       -0.002723110971287527
21       -0.001988207029831428
22      -0.0013311628919007229
23      -0.0008802713399963533
24      -0.0005857080104214093
25     -0.00016530579614282195
26      0.00042337846631840606
27       0.0011978412855764191
28       0.0020898219631927594
29        0.002977749420007403
                ...     

In [45]:
fig, axs = plt.subplots(1,3)
legend = []

for col in dfJ.columns:

    legend.append(col)
#     print(dfdeltaC)

    axs[0].scatter(dfdeltaC[col],dfJ[col]*1e10, marker = '+', s = 10)
    print(dfJ[col])

    axs[1].plot(dt*np.arange(0,len(dfC[col])),dfC[col])

    
#     gradients = []
#     win = 10
#     for i in range(dfJ[col].shape[0]-(win-1)):
        
#         gradient = np.mean(np.gradient(dfJ[col].iloc[i:i+win]))
#         gradients.append(gradient)
        
    
    axs[2].plot(np.gradient(dfJ[col],dfdeltaC[col]))
axs[0].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[1].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[0].set_xlabel('[K_ext]-[K_int] [mM]',fontsize = 18)

axs[0].set_ylabel('J [molm^-2s^-1]',fontsize = 18)

axs[1].set_ylabel('[K_int] [mM]',fontsize = 18)


axs[1].set_xlabel(' T [mins]',fontsize = 18)


#xticks

axs[0].set_xticks([0,0.5,1])
axs[0].set_xticklabels([0,0.5,1],fontsize = 15)
axs[0].set_xlim([0,1.05])

axs[1].set_xticks([0,60,120])
axs[1].set_xticklabels([0,60,120],fontsize = 15)

#yticks

axs[0].set_yticks([0,0.01,0.02])
axs[0].set_yticklabels([0,0.01,0.02],fontsize = 15)

axs[0].set_ylim([-0.0005,0.0105])
axs[1].set_yticks([0, 0.5,1])
axs[1].set_yticklabels([0,0.5,1],fontsize = 15)


axs[0].set_ylim([-0.0005,0.0205])
axs[1].set_ylim([-0.05,1.05])


plt.legend(legend)
# plt.rcParams['text.usetex'] = True

# def myticks(x,pos):

#     if x == 0: return "$0$"

#     exponent = int(np.log1

#     coeff = x/10**exponent

#     return r"${:2.0f} \times 10^{{ {:2d} }}$".format(coeff,exponent)

# axs[0].yaxis.set_major_formatter(ticker.FuncFormatter(myticks))

0     -4.540195e-10
1     -4.542537e-10
2     -4.547222e-10
3     -4.551910e-10
4     -4.556599e-10
5     -4.561289e-10
6     -4.565982e-10
7     -4.570676e-10
8     -4.575372e-10
9     -4.869056e-10
10    -5.456844e-10
11    -5.118031e-10
12    -3.750622e-10
13    -3.305772e-10
14    -3.438702e-10
15    -2.339757e-10
16    -5.333380e-11
17     1.068732e-10
18     3.310654e-10
19     4.203626e-10
20     2.790262e-10
21     1.390624e-10
22     2.012581e-10
23     4.419420e-10
24     5.376526e-10
25     4.837098e-10
26     4.464479e-10
27     4.057467e-10
28     4.460094e-10
29     5.761519e-10
           ...     
504    1.799729e-10
505    2.001523e-10
506    1.232857e-10
507    3.363235e-11
508    1.384532e-12
509    9.000228e-11
510    1.424844e-10
511    1.410444e-10
512    1.465055e-10
513    5.139807e-11
514   -1.498588e-10
515   -1.122579e-10
516    1.109388e-11
517   -2.774639e-13
518   -9.397674e-12
519    4.080175e-11
520    1.699932e-10
521    1.465201e-10
522    4.866890e-11


0      1.397397e-09
1      1.395800e-09
2      1.392605e-09
3      1.389413e-09
4      1.386224e-09
5      1.383037e-09
6      1.379853e-09
7      1.376672e-09
8      1.373493e-09
9      1.332640e-09
10     1.155651e-09
11     9.700666e-10
12     8.342448e-10
13     7.257003e-10
14     7.230480e-10
15     7.889168e-10
16     6.922549e-10
17     4.648303e-10
18     2.707047e-10
19     1.237997e-10
20     1.350662e-10
21     1.752404e-10
22     1.303567e-10
23     8.784670e-11
24     6.058411e-11
25     8.528662e-11
26     2.953929e-10
27     4.039845e-10
28     2.994525e-10
29     4.584453e-10
           ...     
504    3.752126e-10
505    3.520985e-10
506    3.013444e-10
507    2.866549e-10
508    3.350393e-10
509    2.275891e-10
510    7.852272e-11
511    4.702587e-11
512   -8.004576e-11
513   -1.383346e-10
514   -6.048489e-11
515   -6.346798e-11
516   -6.982075e-11
517   -2.568393e-12
518    5.662172e-11
519    9.460413e-11
520    8.066110e-11
521    3.848387e-11
522    7.439861e-11


0     -6.034316e-10
1     -6.036537e-10
2     -6.040978e-10
3     -6.045420e-10
4     -6.049864e-10
5     -6.054309e-10
6     -6.058755e-10
7     -6.063202e-10
8     -6.067651e-10
9     -6.040996e-10
10    -5.995679e-10
11    -5.722960e-10
12    -5.848256e-10
13    -6.436873e-10
14    -6.308453e-10
15    -5.196487e-10
16    -3.920085e-10
17    -4.226351e-10
18    -5.028523e-10
19    -5.036562e-10
20    -4.697650e-10
21    -3.699733e-10
22    -3.067896e-10
23    -3.562089e-10
24    -3.127030e-10
25    -1.652972e-10
26    -3.420355e-11
27     2.598865e-11
28    -1.319026e-11
29     2.875728e-11
           ...     
504    4.504463e-10
505    4.630865e-10
506    5.558390e-10
507    6.353704e-10
508    5.106561e-10
509    3.422123e-10
510    2.501780e-10
511    1.648432e-10
512    1.065180e-10
513    1.046432e-10
514    1.456460e-10
515    1.792940e-10
516    1.593637e-10
517    1.243277e-10
518    1.084787e-10
519    8.531541e-11
520    2.385543e-11
521   -2.713625e-11
522   -6.542356e-11


0      6.900511e-10
1      6.897445e-10
2      6.891314e-10
3      6.885185e-10
4      6.879056e-10
5      6.872929e-10
6      6.866804e-10
7      6.860679e-10
8      6.854556e-10
9      6.288913e-10
10     5.890774e-10
11     6.173358e-10
12     5.541049e-10
13     4.942302e-10
14     4.001410e-10
15     2.458811e-10
16     1.733029e-10
17     1.111191e-10
18     1.696706e-11
19    -1.977989e-11
20     1.292650e-11
21    -6.609660e-11
22    -2.206436e-10
23    -2.483857e-10
24    -2.070142e-10
25    -1.609088e-10
26    -2.247328e-10
27    -3.533206e-10
28    -3.314507e-10
29    -4.113680e-10
           ...     
504    5.433411e-10
505    5.558991e-10
506    5.786104e-10
507    5.214874e-10
508    5.276302e-10
509    5.451508e-10
510    5.070310e-10
511    5.038803e-10
512    5.493706e-10
513    5.644852e-10
514    5.475295e-10
515    4.732239e-10
516    4.018775e-10
517    3.076434e-10
518    2.352681e-10
519    1.964675e-10
520    2.095481e-10
521    2.162781e-10
522    1.402689e-10


0      1.499951e-10
1      1.499756e-10
2      1.499367e-10
3      1.498978e-10
4      1.498589e-10
5      1.498199e-10
6      1.497810e-10
7      1.497421e-10
8      1.497032e-10
9      8.207675e-11
10     1.358231e-10
11     2.573136e-10
12     2.885746e-10
13     3.832801e-10
14     4.262428e-10
15     3.464226e-10
16     2.907242e-10
17     2.405040e-10
18     1.495055e-10
19     1.709186e-10
20     2.599883e-10
21     3.498189e-10
22     3.683521e-10
23     5.118470e-10
24     7.362729e-10
25     9.333267e-10
26     1.078004e-09
27     1.141492e-09
28     1.268113e-09
29     1.007796e-09
           ...     
504    1.570337e-10
505    3.514722e-10
506    4.134262e-10
507    6.510438e-10
508    7.996904e-10
509    7.826839e-10
510    8.513534e-10
511    8.541853e-10
512    8.137985e-10
513    7.411435e-10
514    6.163661e-10
515    5.000879e-10
516    4.826320e-10
517    3.673706e-10
518    3.165178e-10
519    3.613536e-10
520    2.736775e-10
521    1.584810e-10
522    5.122538e-11


/home/marcus/anaconda3/lib/python3.7/site-packages/numpy/lib/function_base.py:1069: RuntimeWarning: divide by zero encountered in double_scalars
  a = -(dx2)/(dx1 * (dx1 + dx2))
/home/marcus/anaconda3/lib/python3.7/site-packages/numpy/lib/function_base.py:1071: RuntimeWarning: divide by zero encountered in double_scalars
  c = dx1 / (dx2 * (dx1 + dx2))


In [63]:
%matplotlib qt
figJ, axJ = plt.subplots(1,1)
figC, axC = plt.subplots(1,1)



def Jfit(deltac,k,c):
    return k*deltac + c

p0 = [1e-14,0]
Pparams = {}
for i,col in enumerate(dfJ.columns):
    

    t = dt*np.arange(0,len(dfC[col]))
    
    J = dfJ[col].iloc[t > 0]
    deltaC = dfdeltaC[col].iloc[t > 0]
    
#     deltaC_bar = np.linspace(dfC[col].min(),1)
    params = curve_fit(Jfit,deltaC.iloc[deltaC.to_numpy().astype(float)>0.8],J.iloc[deltaC.to_numpy().astype(float)>0.8],p0)    
    J_bar = Jfit(deltaC.iloc[deltaC.to_numpy().astype(float)>0.8],*params[0])
    P = params[0][0]
    dP = np.sqrt(params[1][0][0])
    print(dP/P, P)
    

    
    if  P < 0:
        
        continue
        
    Pparams[col] = params
#     if len(J.iloc[(deltaC < 0.7).to_numpy()]) < 1:
#         continue
#     print(col)
   
    # plot fluxes
    axJ.scatter(deltaC,J,alpha = 0.25)
    axJ.plot(deltaC.iloc[deltaC.to_numpy().astype(float)>0.8],J_bar)
    
    #plot the Intensity vs time
    
    axC.plot(t,dfI[col].iloc[t0:t1])
 
#Flux plot params


axJ.set_xticks([0,0.5,1])
axJ.set_xlim([-0.05,1.05])
axJ.set_xticklabels([0,0.5,1],fontsize = 15)

axJ.set_xlabel('$[K]_{ext} - [K]_{in}$ [mM]',fontsize = 18)
axJ.set_yticks([0,2.5e-9,5e-9,7.5e-9,1e-8])
axJ.set_yticklabels([0,2.5,5,7.5,10],fontsize = 15)

axJ.set_ylim([-2e-9,1.2e-8])
    
axJ.set_ylabel('J  [$10^{-9}$ mol$m^{-2}s^{-1}$]',fontsize = 18)
axJ.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)

axC.set_xticks([0,20,40])
axC.set_xticklabels([0,20,40],fontsize = 15)
axC.set_xlabel('Time [mins]',fontsize = 18)
axC.set_xlim([-2,45])
axC.set_yticks([0,0.5,1])
axC.set_yticklabels([0,0.5,1],fontsize = 15)
axC.set_ylabel('Rel I',fontsize = 18 )
axC.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)
axC.set_ylim([-0.05,1.05])

# global params

# plt.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)

2.373344388208225 3.2943704999493387e-10
-0.6241749377577044 -1.4670283958063659e-09
0.6062686085977179 9.224391431108434e-10
2.9082177792106942 4.10076428806716e-10
-0.2467241396479424 -3.529199470326875e-09
-0.9601179849362131 -3.0442458058633654e-10
-0.873188488468394 -7.481266305133982e-10
29.32845170795477 1.8263312810180283e-11
-0.27230369754302475 -2.671869550137193e-09
2.2007470682016015 8.044236928365025e-10
0.4510957570185408 7.507519724114571e-10
0.14602142007325664 3.3770471006758284e-09
1.633769432762354 4.645825604233821e-10
1.4769597939621153 2.924436478514585e-10
0.4134401621907686 7.559182114999404e-10
0.8585373786555284 1.3691774630414787e-09
0.40757120755612575 1.7702007608389094e-09
-0.17756007887138026 -2.2267924552517e-09
-0.17170384817521836 -8.72906205320993e-09
-0.2735112887377036 -2.720010108487655e-09
0.33359386763830196 1.4952495519523793e-09
-0.8886495118791227 -9.256022807877758e-10
0.4226365690913441 6.255005230118645e-10
-0.9245529672740321 -1.1186740448

(-0.05, 1.05)

# Save permeability values


In [58]:
P_df

Empty DataFrame
Columns: [P ms^-1, dP/P, A, P cms^-1]
Index: []

In [62]:
P_df

P ms^-1       dP/P            A      P cms^-1
0    3.294370e-10   2.373344   902.609601  3.294370e-08
1   -1.467028e-09  -0.624175  2034.252831 -1.467028e-07
2    9.224391e-10   0.606269  1748.743976  9.224391e-08
3    4.100764e-10   2.908218  2028.571060  4.100764e-08
4   -3.529199e-09  -0.246724  2199.499706 -3.529199e-07
5   -3.044246e-10  -0.960118  3159.358560 -3.044246e-08
6   -7.481266e-10  -0.873188  2306.245018 -7.481266e-08
7    1.826331e-11  29.328452  2014.036685  1.826331e-09
8   -2.671870e-09  -0.272304  1828.672101 -2.671870e-07
9    8.044237e-10   2.200747  2422.639289  8.044237e-08
10   7.507520e-10   0.451096  2627.810643  7.507520e-08
11   3.377047e-09   0.146021  1603.899706  3.377047e-07
12   4.645826e-10   1.633769  2204.343976  4.645826e-08
13   2.924436e-10   1.476960  1457.698143  2.924436e-08
14   7.559182e-10   0.413440  2838.921060  7.559182e-08
15   1.369177e-09   0.858537  3347.309601  1.369177e-07
16   1.770201e-09   0.407571  1046.863247  1.770201e-07
17  -2.226792e-09  -0.177560   860.533039 -2.226792e-07
18  -8.729062e-09  -0.171704   831.685643 -8.729062e-07
19  -2.720010e-09  -0.273511  2054.475226 -2.720010e-07
20   1.495250e-09   0.333594  1650.420203  1.495250e-07
21  -9.256023e-10  -0.888650  1243.645724 -9.256023e-08
22   6.255005e-10   0.422637  1431.178016  6.255005e-08
23  -1.118674e-09  -0.924553  2848.759786 -1.118674e-07
24   3.743041e-09   0.122160  1983.197286  3.743041e-07
25   2.640777e-09   0.242124  1676.793120  2.640777e-07
26   7.042218e-09   0.182946  2240.541557  7.042218e-07
27   7.948902e-09   0.066141  3590.976974  7.948902e-07
28   4.699651e-09   0.209212  2536.151974  4.699651e-07
29  -5.096724e-10  -1.639498  2317.116036 -5.096724e-08
..            ...        ...          ...           ...
106  1.867010e-09   0.344916  1695.135691  1.867010e-07
107  1.251316e-09   0.262478  2404.666941  1.251316e-07
108  1.203847e-09   0.282314  2585.092983  1.203847e-07
109 -3.427114e-09  -0.464462  1522.816941 -3.427114e-07
110 -6.221726e-09  -0.132006  1531.741626 -6.221726e-07
111 -1.881890e-09  -0.351551  1248.996314 -1.881890e-07
112 -7.995206e-09  -0.333828  1521.118710 -7.995206e-07
113  4.200957e-09   0.146219   994.261939  4.200957e-07
114  2.636151e-10   1.435732  1416.110897  2.636151e-08
115  1.585150e-09   0.310076  2130.645272  1.585150e-07
116 -1.048879e-10  -4.409276  1846.893189 -1.048879e-08
117 -1.283281e-09  -0.516885  1421.298918 -1.283281e-07
118 -1.641699e-09  -0.646424  2203.167147 -1.641699e-07
119 -1.671456e-10  -3.159305  2702.049960 -1.671456e-08
120  4.209727e-11  29.243021  1767.308409  4.209727e-09
121 -1.683353e-09  -0.794731  2069.661013 -1.683353e-07
122  6.064036e-10   0.672774  2246.814138  6.064036e-08
123  2.647347e-09   0.157547  1236.974555  2.647347e-07
124 -1.839389e-09  -0.667982  1826.275076 -1.839389e-07
125 -7.238079e-10  -1.147119  1391.208930 -7.238079e-08
126 -1.001786e-09  -0.557225  2345.386013 -1.001786e-07
127 -5.251337e-10  -1.633939  1533.817263 -5.251337e-08
128 -4.428318e-10  -0.605611  1335.028201 -4.428318e-08
129  2.591993e-09   0.486455  2657.162055  2.591993e-07
130  1.218288e-09   0.253405  3481.881326  1.218288e-07
131 -3.384933e-09  -0.366459  2443.976638 -3.384933e-07
132  3.102398e-09   0.321341  2148.646430  3.102398e-07
133  2.276440e-09   0.137739  1009.943305  2.276440e-07
134  7.821225e-10   0.692614   923.942263  7.821225e-08
135  6.809425e-10   0.936802  2068.735492  6.809425e-08

[136 rows x 4 columns]

In [59]:
P_df = {'P ms^-1': [Pparams[key][0][0] for key in Pparams.keys()],
       'dP/P': [np.sqrt(Pparams[key][1][0][0])/Pparams[key][0][0] for key in Pparams.keys()],
       'A':[np.mean(dfA[key].iloc[:30]) for key in Pparams.keys()]}
        
P_identified = {key:[Pparams[key][0][0]] for key in Pparams.keys()}
P_df = pd.DataFrame(P_df)
P_identified = pd.DataFrame(P_identified)
P_df['P cms^-1'] = P_df['P ms^-1']*100

P_df.to_csv('Permeabilities_GramicidinA_260pM20210920.csv')

# Save Flux vs deltaC data

In [60]:
dfJ.to_csv('Flux_GramA_260pM_20210920.csv')
dfdeltaC.to_csv('deltaC_GramA_260pM_20210920.csv')
P_identified.to_csv('PbyGUVId_GramA_260pM_20210920.csv')

# The relationship between J and delta c

The variation of the flux, J, with $\Delta c$ is linear. However in order to gain a good fit, we have to relax ths condition that the flux is zero when the gradient is 0. 

Near to 1mM internal concentration the calibration underestimates the internal concentration. Therefore it overestimates the concentration gradient at the point of zero flux. This develops an associated error in the y intercept and the permeability.


In [206]:
JoverP = {}

for col in dfJ.columns:
    
    P = Pparams[col][0][0]
    dP = np.sqrt(Pparams[col][1][0][0])
    
    if dP/P > 0.1 or P < 0:
        
        continue
    
    JoverP[col] = dfJ[col]/P
    
dfJoverP = pd.DataFrame(JoverP)


fig, ax = plt.subplots(1,1)

for col in dfJoverP.columns:
    
    ax.scatter(dfdeltaC[col],dfJoverP[col])
    

/home/marcus/anaconda3/lib/python3.7/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)


In [156]:
axs[2].cla()